## COVID-19 Vaccines Project - Choropleth and Scatter with Plotly


### Objectives:
* Create a choropleth and scatter plot with Plotly to show Covid vaccinations
* Create and manipulate Pandas DFs with data inputted from open source data

In [1]:
# Import standard dependencies
import pandas as pd
from plotly import express as px
from datetime import datetime
import numpy as np
import plotly.graph_objects as go
import datetime as dt


## Retrieve and process new case data

In [2]:
# cases data https://data.cdc.gov/api/views/9mfq-cb36/rows.csv
url = 'https://data.cdc.gov/api/views/9mfq-cb36/rows.csv'

#read csv
df_case = pd.read_csv(url, 
                      usecols = ['submission_date','state','new_case'])

#test
df_case    

submission_date state  new_case
0          01/14/2022    KS     19414
1          01/02/2022    AS         0
2          01/30/2022    CO         0
3          07/09/2020    CO       410
4          01/26/2022    CO      6962
...               ...   ...       ...
47215      06/07/2020    SD        71
47216      12/28/2021    NY     13006
47217      09/25/2021   RMI         0
47218      06/19/2021    TN       182
47219      03/13/2021    IA       425

[47220 rows x 3 columns]

In [3]:
#rename columns
df_case.rename(columns = {'new_case':'cases', 'submission_date':'date'}, inplace = True)

#convert date from integer yyyymmdd to date format
df_case["date"]= pd.to_datetime(df_case["date"])

#change index to date
df_case.set_index(['date'], inplace=True)

df_case


state  cases
date                   
2022-01-14    KS  19414
2022-01-02    AS      0
2022-01-30    CO      0
2020-07-09    CO    410
2022-01-26    CO   6962
...          ...    ...
2020-06-07    SD     71
2021-12-28    NY  13006
2021-09-25   RMI      0
2021-06-19    TN    182
2021-03-13    IA    425

[47220 rows x 2 columns]

In [4]:
# Show the odd entries in MO for 4/17 and 4/19 since

df_case.at['04/17/2021','cases']='320'
df_case.at['04/19/2021','cases']='320'

In [5]:
#sets the temp df equal to the df
df_temp = df_case

#creates 7 day moving average column in df
df_temp['7D_sum'] = df_temp['cases'].rolling(7).sum()

#removes NANs from new column
df_temp['7D_sum'] = df_temp['7D_sum'].fillna(0)

df_temp   # confirm new df_temp output

state  cases   7D_sum
date                            
2022-01-14    KS  19414      0.0
2022-01-02    AS      0      0.0
2022-01-30    CO      0      0.0
2020-07-09    CO    410      0.0
2022-01-26    CO   6962      0.0
...          ...    ...      ...
2020-06-07    SD     71   6779.0
2021-12-28    NY  13006  19056.0
2021-09-25   RMI      0  19056.0
2021-06-19    TN    182  14344.0
2021-03-13    IA    425  14248.0

[47220 rows x 3 columns]

In [6]:
# merge cases7D_sum into the original dataframe

df_case['7D_sum'] = df_temp['7D_sum']

df_case.tail(10)

state  cases   7D_sum
date                            
2021-01-12   RMI      0  10147.0
2022-01-31    PA   4894  14397.0
2022-03-14    NY    521  14861.0
2021-07-14    NY    336   8680.0
2020-05-28    IA    228   6708.0
2020-06-07    SD     71   6779.0
2021-12-28    NY  13006  19056.0
2021-09-25   RMI      0  19056.0
2021-06-19    TN    182  14344.0
2021-03-13    IA    425  14248.0

In [7]:
# Confirm that merge worked properly. Manually sum the 7 cases in the output below.
df_case[df_case['state']=="WI"].tail(7)

state  cases   7D_sum
date                            
2021-12-19    WI      0   2615.0
2020-10-14    WI   3323   7546.0
2021-05-13    WI    571   7846.0
2022-01-19    WI  14760  23268.0
2020-05-11    WI    199   4711.0
2021-07-25    WI    320  12724.0
2022-02-23    WI   1088   4043.0

In [8]:
#get data
url2 = 'https://data.cdc.gov/api/views/unsk-b7fc/rows.csv'

#getting df_vax data
df_vax = pd.read_csv(url2, 
                      usecols = ['Date','Location','Series_Complete_Yes'])


In [9]:
#rename columns
df_vax.rename(columns = {'Date':'date', 'Location':'state', 'Series_Complete_Yes':'vax_complete'}, inplace = True)

#convert date from integer yyyymmdd to date format
df_vax["date"]= pd.to_datetime(df_vax["date"])

#change index to date
df_vax.set_index(['date'], inplace=True)

#check what Wisconsin's data is like
df_vax[df_vax['state']=='WI']

state  vax_complete
date                          
2022-03-19    WI       3781421
2022-03-18    WI       3780383
2022-03-17    WI       3779552
2022-03-16    WI       3778622
2022-03-15    WI       3777764
...          ...           ...
2020-12-18    WI             0
2020-12-17    WI             0
2020-12-16    WI             0
2020-12-15    WI             0
2020-12-14    WI             0

[461 rows x 2 columns]

In [10]:
# This dictionary include population projections for US states and territories for 2019.  Used to merge with the df.
state_pop ={
 'AL': 4903185,
 'AK': 731545,
 'AZ': 7278717,
 'AR': 3017804,
 'CA': 39512223,
 'CO': 5758736,
 'CT': 3565287,
 'DE': 973764,
 'DC': 705749,
 'FL': 21477737,
 'GA': 10617423,
 'HI': 1415872,
 'ID': 1787065,
 'IL': 12671821,
 'IN': 6732219,
 'IA': 3155070,
 'KS': 2913314,
 'KY': 4467673,
 'LA': 4648794,
 'ME': 1344212,
 'MD': 6045680,
 'MA': 6892503,
 'MI': 9986857,
 'MN': 5639632,
 'MS': 2976149,
 'MO': 6137428,
 'MT': 1068778,
 'NE': 1934408,
 'NV': 3080156,
 'NH': 1359711,
 'NJ': 8882190,
 'NM': 2096829,
 'NY': 19453561,
 'NC': 10488084,
 'ND': 762062,
 'OH': 11689100,
 'OK': 3956971,
 'OR': 4217737,
 'PA': 12801989,
 'RI': 1059361,
 'SC': 5148714,
 'SD': 884659,
 'TN': 6829174,
 'TX': 28995881,
 'UT': 3205958,
 'VT': 623989,
 'VA': 8535519,
 'WA': 7614893,
 'WV': 1792147,
 'WI': 5822434,
 'WY': 578759}

## Merge dataframes, create population related data 
* Merge on state and date
* Calculate Rolling 7 Day cases per 100K population
* Caclulate Percent Population Fully Vaccinated

In [11]:
# Merge the case and vax dataframes into a single dataframe name df

#inner join both df into a single df
df = pd.merge(df_case, df_vax, on=['date','state'], how='inner')

# ^^^ Your code above
df

state  cases   7D_sum  vax_complete
date                                          
2022-01-14    KS  19414      0.0       1683502
2022-01-02    AS      0      0.0         32705
2022-01-30    CO      0      0.0       3927291
2022-01-26    CO   6962      0.0       3915242
2022-01-01    UT      0  26786.0       1885145
...          ...    ...      ...           ...
2022-03-14    NY    521  14861.0      14759477
2021-07-14    NY    336   8680.0      10808066
2021-12-28    NY  13006  19056.0      13927276
2021-06-19    TN    182  14344.0       2345119
2021-03-13    IA    425  14248.0        407675

[25808 rows x 4 columns]

In [12]:
### Population based transformations and calculations

df['cases'] = df['cases'].astype(int)
df['7D_sum'] = df['7D_sum'].astype(int)
df['vax_complete'] = df['cases'].astype(int)

# map 'pop' to each row in df based on state_pop dictionary
df['pop'] = df['state'].map(state_pop)

# add 'vax_rate as vax_complete / population estimate for state
df['vax_rate'] = df['vax_complete']/df['pop']

# add 'cases7D_100K' as cases over 7D divided by pop times 100K
df['cases7d_100k'] = df['cases'] / df['7D_sum'] / df['pop'] * 100000

# Your code above, code below to confirm data for one state

df[df['state']=='WI']

state  cases  7D_sum  vax_complete        pop  vax_rate  \
date                                                                 
2022-01-01    WI      0    2950             0  5822434.0  0.000000   
2021-09-09    WI   2095    7272          2095  5822434.0  0.000360   
2022-03-02    WI    781    9347           781  5822434.0  0.000134   
2021-11-20    WI      0    1974             0  5822434.0  0.000000   
2021-09-14    WI   2488    9110          2488  5822434.0  0.000427   
...          ...    ...     ...           ...        ...       ...   
2021-12-19    WI      0    2615             0  5822434.0  0.000000   
2021-05-13    WI    571    7846           571  5822434.0  0.000098   
2022-01-19    WI  14760   23268         14760  5822434.0  0.002535   
2021-07-25    WI    320   12724           320  5822434.0  0.000055   
2022-02-23    WI   1088    4043          1088  5822434.0  0.000187   

            cases7d_100k  
date                      
2022-01-01      0.000000  
2021-09-09      0.004948  
2022-03-02      0.001435  
2021-11-20      0.000000  
2021-09-14      0.004691  
...                  ...  
2021-12-19      0.000000  
2021-05-13      0.001250  
2022-01-19      0.010895  
2021-07-25      0.000432  
2022-02-23      0.004622  

[460 rows x 7 columns]

In [13]:
#only modern dates so the df won't crash
df = df[(df.index >= '2021-03-01')]

In [14]:
# resave data frame to only include rows where pop > 0

df = df[(df['pop'] > 0)]

In [15]:
df.reset_index(drop=False, inplace = True)
df

date state  cases  7D_sum  vax_complete         pop  vax_rate  \
0     2022-01-14    KS  19414       0         19414   2913314.0  0.006664   
1     2022-01-30    CO      0       0             0   5758736.0  0.000000   
2     2022-01-26    CO   6962       0          6962   5758736.0  0.001209   
3     2022-01-01    UT      0   26786             0   3205958.0  0.000000   
4     2021-05-22    MA    451    7823           451   6892503.0  0.000065   
...          ...   ...    ...     ...           ...         ...       ...   
19528 2022-03-14    NY    521   14861           521  19453561.0  0.000027   
19529 2021-07-14    NY    336    8680           336  19453561.0  0.000017   
19530 2021-12-28    NY  13006   19056         13006  19453561.0  0.000669   
19531 2021-06-19    TN    182   14344           182   6829174.0  0.000027   
19532 2021-03-13    IA    425   14248           425   3155070.0  0.000135   

       cases7d_100k  
0               inf  
1               NaN  
2               inf  
3          0.000000  
4          0.000836  
...             ...  
19528      0.000180  
19529      0.000199  
19530      0.003508  
19531      0.000186  
19532      0.000945  

[19533 rows x 8 columns]

In [16]:
#replace infinity with NaN for cases7d_100k
df.replace([np.inf, -np.inf], np.nan, inplace=True)

#drop all NaNs
df.dropna(subset=["cases7d_100k"], how="all")

date state  cases  7D_sum  vax_complete         pop  vax_rate  \
3     2022-01-01    UT      0   26786             0   3205958.0  0.000000   
4     2021-05-22    MA    451    7823           451   6892503.0  0.000065   
5     2021-10-26    HI     69    8511            69   1415872.0  0.000049   
6     2021-07-26    OK   1028    9129          1028   3956971.0  0.000260   
7     2021-10-23    GA      0    3582             0  10617423.0  0.000000   
...          ...   ...    ...     ...           ...         ...       ...   
19528 2022-03-14    NY    521   14861           521  19453561.0  0.000027   
19529 2021-07-14    NY    336    8680           336  19453561.0  0.000017   
19530 2021-12-28    NY  13006   19056         13006  19453561.0  0.000669   
19531 2021-06-19    TN    182   14344           182   6829174.0  0.000027   
19532 2021-03-13    IA    425   14248           425   3155070.0  0.000135   

       cases7d_100k  
3          0.000000  
4          0.000836  
5          0.000573  
6          0.002846  
7          0.000000  
...             ...  
19528      0.000180  
19529      0.000199  
19530      0.003508  
19531      0.000186  
19532      0.000945  

[19530 rows x 8 columns]

## Plot 1: Choropleth

In [17]:
# Plot 1
# I could not get the date slider to work properly, I commented out what crashes the code

fig = px.choropleth(df,
                    color = 'vax_rate',
                    title = 'Vax Rate by State',
                    scope = 'usa',
                    locationmode = 'USA-states',
                    color_continuous_scale = 'blugrn',
                    locations = 'state',
                    hover_name = 'state'#,
                    #animation_frame = 'date'
                   )

fig.show()

## Plot 2: Scatter_Geo Plot

In [18]:
# Plot 3: Scatter Geo with Normalized Case Data
#The size here is not working so I commented it out.  I am unsure why it is not working.

fig3 = px.scatter_geo(df,
                        title = 'Vax Rate by State (color) and 7 Day Sum of Cases per 100k Population (size)',
                        color = 'vax_rate',
                        scope = 'usa',
                        locationmode = 'USA-states',
                        color_continuous_scale = 'blugrn',
                        locations = 'state',
                        hover_name = 'state',
                        #size = 'cases7D_100k'
                        #animation_frame = 'date'
                       )

fig3.show()
